In [18]:
import numpy as np
import pandas as pd
import gtda.time_series 
import plotly
from scipy.sparse import csr_matrix
import networkx as nx
import matplotlib.pyplot as plt

Daten import von https://data.europa.eu/data/datasets/ilkley-moor-water-level-monitor7?locale=de

In [19]:
water_level_data=pd.read_csv('./Ilkley_Moor_Water_Level_Monitor.csv')

In [20]:
water_level_data

OBJECTID        FLOW  WATER_LEVEL                   DATE_  SHAPEAREA  \
0             1  403.427734        0.364  2019/10/08 05:30:00+00     750000   
1             2  403.427734        0.364  2019/10/08 05:45:00+00     750000   
2             3  403.427734        0.364  2019/10/08 06:00:00+00     750000   
3             4  403.427734        0.364  2019/10/08 06:15:00+00     750000   
4             5  403.427734        0.364  2019/10/08 06:30:00+00     750000   
...         ...         ...          ...                     ...        ...   
91978    113116    0.000309        0.110  2022/03/28 04:30:00+00     750000   
91979    113117    0.000343        0.111  2022/03/28 04:45:00+00     750000   
91980    113118    0.000343        0.111  2022/03/28 05:00:00+00     750000   
91981    113119    0.000343        0.111  2022/03/28 05:15:00+00     750000   
91982    113120    0.000423        0.113  2022/03/28 05:30:00+00     750000   

          SHAPELEN  
0      3236.067977  
1      3236.067977  
2      3236.067977  
3      3236.067977  
4      3236.067977  
...            ...  
91978  3236.067977  
91979  3236.067977  
91980  3236.067977  
91981  3236.067977  
91982  3236.067977  

[91983 rows x 6 columns]

In [168]:
Time_serie=water_level_data.loc[:,"WATER_LEVEL"]

In [197]:
plotly.graph_objects.Figure(data=plotly.graph_objects.Scatter(x=water_level_data.loc[:,"DATE_"], y=Time_serie))

In [171]:
para=gtda.time_series.takens_embedding_optimal_parameters(Time_serie, max_time_delay=600, max_dimension=20)

In [172]:
para

(586, 16)

In [173]:
embedder_periodic = gtda.time_series.SingleTakensEmbedding(
    parameters_type="fixed",
    n_jobs=2,
    time_delay=para[0],
    dimension=para[1]
)

In [174]:
y_periodic_embedded = embedder_periodic.fit_transform(Time_serie)

In [175]:
print(f"Shape of embedded time series: {y_periodic_embedded.shape}")

Shape of embedded time series: (83193, 16)


In [198]:
reihenfolge = np.argsort(y_periodic_embedded)
permutationen = np.unique(reihenfolge, axis=0, return_inverse=True)

In [208]:
len(permutationen[1][0:(len(permutationen[1])-1)])

83192

In [209]:
rows=permutationen[1][1:]
cols=permutationen[1][0:(len(permutationen[1])-1)]
d = {'col1': rows, 'col2':cols}
df = pd.DataFrame(data=d)

In [210]:
df=df[df['col1']!=df['col2']]

In [185]:
values, counts = np.unique(df, return_counts=True, axis=0)

In [211]:
df.drop_duplicates()

col1   col2
3       5947   5946
4       5946   5947
6       5952   5946
7       5950   5952
9       5949   5950
...      ...    ...
83180  25529  25535
83186  25533  25529
83189  25532  25533
83190  25530  25532
83191  25531  25530

[35813 rows x 2 columns]

In [212]:
G = nx.from_pandas_edgelist(df, 'col1', 'col2',create_using=nx.DiGraph)


In [214]:
#tg = np.any(transition_graph)
#g = nx.from_scipy_sparse_matrix(tg, create_using=nx.DiGraph)
nx.draw_networkx(G,node_size=100,with_labels=False)
plt.show()

KeyboardInterrupt: 

In [193]:
ggd = GraphGeodesicDistance(directed=True)
dm = ggd.fit_transform([transition_graph])

In [194]:
from gtda.graphs import GraphGeodesicDistance
from gtda.homology import FlagserPersistence
from gtda.plotting import plot_point_cloud

In [195]:
fp = FlagserPersistence(homology_dimensions = (0,1), n_jobs=-1)
hom = fp.fit_transform(dm)
fp.plot(hom)